In [13]:
import numpy as np
from trimesh import Trimesh
import trimesh

In [ ]:
verts = np.array([[0,0,0], [0,0,1], [0,1,0]])
faces = np.array([0,2,1])
# vertex_colours = np.array([[100,100,100,255],[150,150,150,255],[200,200,200,255]])
vertex_colours = np.array([255,0,0,255])

mesh = Trimesh(verts, faces, vertex_colors=vertex_colours)#, face_colors=face_colours)

mesh.show()

[  3 252 248 255]
<class 'numpy.ndarray'>


In [36]:
import numpy as np
from trimesh import Trimesh

# Define vertices and faces
verts = np.array([[0, 0, 0],
                  [0, 0, 1],
                  [0, 1, 0]])

faces = np.array([[0, 2, 1]])  # Make sure this is 2D

# Define one RGBA color per vertex
vertex_colours = np.array([[255, 0, 0, 255],   # Red
                           [0, 255, 0, 255],   # Green
                           [0, 0, 255, 255]])  # Blue

print(verts.shape)
print(vertex_colours.shape)

# Create the mesh
mesh = Trimesh(vertices=verts, faces=faces, vertex_colors=vertex_colours)

# Visualize
mesh.show()


(3, 3)
(3, 4)


In [37]:
import pickle
from superprimitive_fusion.utils import get_integer_segments, triangulate_segments
with open('../data/kfs_moge_realsense/kf_51.pkl', 'rb') as file:
    data = pickle.load(file)
image_raw = data['state_dict']['image_raw'].cpu().permute(1,2,0)
sp_regions = data['state_dict']['sp_regions'].cpu().numpy()
verts = data['state_dict']['pointmap'].cpu().reshape(-1, 3)

In [48]:
colours_A = data['state_dict']['image_raw'].cpu().permute(1,2,0).reshape(-1,3)
colours_A_4chnl = np.hstack([colours_A,np.ones((colours_A.shape[0],1))])
colours_A_255 = (colours_A_4chnl*255).astype('uint8')
print(colours_A_255)

[[ 18  36  26 255]
 [ 15  35  24 255]
 [ 16  36  27 255]
 ...
 [ 58  76  88 255]
 [ 58  76  88 255]
 [ 59  79  90 255]]


In [ ]:
integer_segments = get_integer_segments(sp_regions)

tris = triangulate_segments(verts, integer_segments)
all_tris = [tri for trise in tris for tri in trise]

In [51]:
mesh = Trimesh(vertices=verts, faces=all_tris, vertex_colors=colours_A_255)
mesh.show()

In [82]:
import numpy as np
import cv2

# Define a small point cloud (6 points in 3D space)
points = np.array([
    [0.0, 0.0, 0.0],
    [1.0, 1.0, 1.0],
    [2.0, 2.0, 2.0],
    [0.5, 0.5, 0.5],
    [1.5, 1.5, 1.5],
    [3.0, 3.0, 3.0]
], dtype=np.float32)

# Query point
query = np.array([[1.2, 1.2, 1.2]], dtype=np.float32)

# Set up FLANN parameters
index_params = dict(algorithm=1, trees=5)  # 1 = KDTree
search_params = dict(checks=50)

# Create FLANN matcher
flann = cv2.flann_Index(points, index_params)

# Find 2 nearest neighbors
k = 2
idx, dists = flann.knnSearch(query, k, params=search_params)

# Output results
print("Query point:", query[0])
print("Indices of nearest neighbors:", idx[0])
print("Distances to nearest neighbors:", dists[0])
print("Nearest neighbor points:", points[idx[0]])


Query point: [1.2 1.2 1.2]
Indices of nearest neighbors: [1 4]
Distances to nearest neighbors: [0.12000005 0.26999992]
Nearest neighbor points: [[1.  1.  1. ]
 [1.5 1.5 1.5]]


In [152]:
import open3d as o3d

# Define a small point cloud (6 points in 3D space)
points = np.array([
    [0.0, 0.0, 0.0],
    [1.0, 1.0, 1.0],
    [2.0, 2.0, 2.0],
    [0.5, 0.5, 0.5],
    [1.5, 1.5, 1.5],
    [3.0, 3.0, 3.0]
], dtype=np.float32)

# Query point
query = np.array([1.2, 1.2, 1.2], dtype=np.float32)

tree = o3d.geometry.KDTreeFlann(points.transpose())

def print_results(N, points, idxs, dists):
    if len(idxs) < 2:
        return
    p = [[float(num) for num in points[id]] for id in idxs]
    d = [round(float(np.sqrt(dist)),3) for dist in dists]
    print(f'N={N}, p={p}, d={d}')

N, idxs, dists = tree.search_knn_vector_3d(query, 3)

print_results(N, points, idxs, dists)

N, idxs, dists = tree.search_radius_vector_3d(query, 1.3)

# pnts = np.array([points[id] for id in idxs])
# dsts = [np.linalg.norm(query - point) for point in pnts]
# print(dsts)

print_results(N, points, idxs, dists)

N=3, p=[[1.0, 1.0, 1.0], [1.5, 1.5, 1.5], [0.5, 0.5, 0.5]], d=[0.346, 0.52, 1.212]
N=3, p=[[1.0, 1.0, 1.0], [1.5, 1.5, 1.5], [0.5, 0.5, 0.5]], d=[0.346, 0.52, 1.212]


In [115]:
d = np.linalg.norm(np.array([0.5,0.5,0.5]) - np.array([1.2,1.2,1.2]))
print(d)
a = 1.212435565298214
b = 1.2124356478888325
a-b

1.212435565298214


-8.259061856641381e-08